In [39]:
import requests
from bs4 import BeautifulSoup
from pathlib import Path
from tqdm import tqdm
import json

In [3]:
this_dir_path = Path().resolve()
data_path = this_dir_path / "Data"
input_verb_path = data_path / "verbs_noor.txt"
htmls_path = data_path / "htmls_noor"
output_verb_path = data_path / "verbs_noor.json"

In [4]:
with open(input_verb_path, "r") as f:
    verbs = [verb[:-1] for verb in f.readlines()]

In [ ]:
for verb in tqdm(verbs):
    response = requests.get("http://search.dadegan.ir/", params={"q": verb})
    with open(htmls_path / (verb + ".html"), "w") as f:
        f.write(response.text)

100%|██████████| 3/3 [00:01<00:00,  2.62it/s]


In [ ]:
results = []

for verb in tqdm(verbs):
    with open(htmls_path / (verb + ".html"), "r") as f:
        text = f.read()
    soup = BeautifulSoup(text, "html.parser")

    stems = soup.findAll("td", {"class": "c3"})[1:]
    past_stem = stems[0].text
    present_stem = stems[1].text

    structures = soup.select("div.section-wrapper.more-examples")
    for structure in structures:
        examples = structure.findAll("div", {"class": "example"})
        for example in examples:
            result = {}
            result["verb"] = verb
            result["past_stem"] = past_stem
            result["present_stem"] = present_stem
            result["structure"] = str(structure.findAll("div", {"class": "valency"})[0])
            result["text"] = example.text
            results.append(result)

100%|██████████| 4167/4167 [00:33<00:00, 122.76it/s]


In [59]:
with open(output_verb_path, "w", encoding="utf-8") as f:
    json.dump(results, f, ensure_ascii=False, indent=4)